In [5]:
import pandas as pd
import altair as alt
from altair import expr, datum
from altair import data_transformers


In [6]:
import panel as pn
pn.extension('vega')

# Make sure that the Panel version is ≥ 0.14.0.
pn.__version__

'0.14.4'

## 1. Load data using pandas

In [7]:
# Enable the "json" data transformer
#alt.data_transformers.enable('json')

In [8]:
#alt.data_transformers.disable_max_rows()

In [9]:
# Load data from the local csv file
data = pd.read_csv('netflix1.csv')

In [10]:
# Size of the data frame (rows * columns)
data.shape

(8790, 10)

In [11]:
# List all variables and their data type
data.dtypes

show_id         object
type            object
title           object
director        object
country         object
date_added      object
release_year     int64
rating          object
duration        object
listed_in       object
dtype: object

In [12]:
# transform date_added from object to datetime 
data['date_added'] = pd.to_datetime(data['date_added'], format='%m/%d/%Y')

# add added_year as a new column 
data['added_year'] = data['date_added'].dt.year

In [13]:
# Get the first rows in the dataset
data = data.head(5000)

data

show_id     type                             title           director  \
0         s1    Movie              Dick Johnson Is Dead    Kirsten Johnson   
1         s3  TV Show                         Ganglands    Julien Leclercq   
2         s6  TV Show                     Midnight Mass      Mike Flanagan   
3        s14    Movie  Confessions of an Invisible Girl      Bruno Garotti   
4         s8    Movie                           Sankofa       Haile Gerima   
...      ...      ...                               ...                ...   
4995   s6882    Movie                              Gook        Justin Chon   
4996   s6883    Movie                              Goon      Michael Dowse   
4997   s6884    Movie   Goosebumps 2: Haunted Halloween         Ari Sandel   
4998   s6885    Movie                      Gosford Park      Robert Altman   
4999   s6887    Movie                           Gothika  Mathieu Kassovitz   

            country date_added  release_year rating  duration  \
0     United States 2021-09-25          2020  PG-13    90 min   
1            France 2021-09-24          2021  TV-MA  1 Season   
2     United States 2021-09-24          2021  TV-MA  1 Season   
3            Brazil 2021-09-22          2021  TV-PG    91 min   
4     United States 2021-09-24          1993  TV-MA   125 min   
...             ...        ...           ...    ...       ...   
4995  United States 2018-03-06          2017  TV-MA    95 min   
4996  United States 2017-08-15          2011      R    92 min   
4997  United States 2019-04-25          2018     PG    90 min   
4998  United States 2019-11-01          2001      R   137 min   
4999  United States 2021-01-01          2003      R    98 min   

                                              listed_in  added_year  
0                                         Documentaries        2021  
1     Crime TV Shows, International TV Shows, TV Act...        2021  
2                    TV Dramas, TV Horror, TV Mysteries        2021  
3                    Children & Family Movies, Comedies        2021  
4      Dramas, Independent Movies, International Movies        2021  
...                                                 ...         ...  
4995                         Dramas, Independent Movies        2018  
4996                            Comedies, Sports Movies        2017  
4997                 Children & Family Movies, Comedies        2019  
4998             Comedies, Dramas, International Movies        2019  
4999                           Horror Movies, Thrillers        2021  

[5000 rows x 11 columns]

## 2. Draw charts

In [14]:
#define color scale
scale = alt.Scale(domain=['United States', 'India', 'Pakistan', 'United Kingdom', 'Not Given', 'Canada','Spain','France','Nigeria','Japan'],
                  range=['#FF5733', '#3D9970','#0074D9','#FFC300','#85144b','#7FDBFF','#F012BE','#2ECC40','#FF851B','#B10DC9'])

color = alt.Color('country:N', scale=scale)

In [15]:
# Create multiple selection on the bar chart
click = alt.selection_multi(encodings=['color'])

# Create interval selecion on the bubble chart
brush = alt.selection_interval(encodings=['x'])


In [16]:
# Group the data by country and count the number of occurrences
grouped_data = data.groupby('country').size().reset_index(name='count')

# Sort the data by count in descending order
sorted_data = grouped_data.sort_values('count', ascending=False)

# Limit the data to the top 10 countries
top_10_data = sorted_data[:10]

# Create an Altair chart with the sorted and limited data
bars = alt.Chart(top_10_data).mark_bar().encode(
    x='count:Q',
    y=alt.Y('country:N', sort='-x')
)    

bars

alt.Chart(...)

In [17]:
bar1 = alt.Chart(data).mark_point().encode(
    x=alt.X('date_added:T', title="added_year"),
    y=alt.Y('count()', title='count'),
    color='type:N'
).interactive()

bar1

alt.Chart(...)

In [18]:
bar1 = alt.Chart(data).mark_bar().encode(
    x=alt.X('date_added:T', title="added_year"),
    y=alt.Y('count()', title='count'),
    color='type:N'
).interactive()

bar1

alt.Chart(...)

# PART 1

In [19]:
import pandas as pd
import altair as alt
import panel as pn
import re

alt.data_transformers.enable('default', max_rows=None)

# read the csv file
df = pd.read_csv("netflix1.csv")

# transform date_added from object to datetime 
df['date_added'] = pd.to_datetime(df['date_added'])

# transform date_added from object to datetime 
df['date_added'] = pd.to_datetime(df['date_added'], format='%m/%d/%Y')

# add added_year as a new column 
df['added_year'] = df['date_added'].dt.year

# descending the duration 
df = df.sort_values(by=['duration'], ascending=False)

In [20]:
# ADD new column
df['Duration'] = None

# when type = movie
movie_mask = df['type'] == 'Movie'
df.loc[movie_mask, 'Duration'] = df.loc[movie_mask, 'duration'].str.extract('(\d+)', expand=False).astype(int)

# when type = tv show
tv_show_mask = df['type'] == 'TV Show'
df.loc[tv_show_mask, 'Duration'] = df.loc[tv_show_mask, 'duration']


In [ ]:
df

In [22]:
brush = alt.selection_interval(name='brush')

# create scatter chart with duration and added year
scatter_chart = alt.Chart(df).mark_point().encode(
        x=alt.X('date_added', title='Date Added'),
        y=alt.Y('duration', title='Duration'),
        color=alt.condition(brush, 'type:N', alt.value('lightgrey')),
        #color=alt.Color('type',scale=alt.Scale(scheme='category20'), legend=None),
        tooltip=['title', 'type', 'date_added', 'duration']
    ).properties(
        title='Date Added vs. Duration'
    ).add_selection(
        brush
    )

#scatter_chart

In [23]:
def generate_plots(country_name, type_name, year_range):
    # fliter by country, type and year
    country_data = df[(df['country'].str.contains(country_name)) & 
                      (df['type'] == type_name) &
                      (df['added_year'].between(year_range[0], year_range[1]))
                     ]

    year_range_slider = pn.widgets.RangeSlider(name='Year Range', start=df['added_year'].min(),
                                           end=df['added_year'].max(), step=1, value=(df['added_year'].min(), df['release_year'].max()))

    # count by type
    count_by_type = country_data.groupby(['type']).size().reset_index(name='count')

    # add brush
    brush = alt.selection_interval()

    # create bar chart with different type
    bar_chart = alt.Chart(count_by_type).mark_bar().encode(
        x=alt.X('count', title='Count'),
        y=alt.Y('type', title='Type', sort=alt.EncodingSortField(field='count', op='sum', order='descending')),
        color=alt.Color('type',scale=alt.Scale(scheme='category20'), legend=None),
        tooltip=['type', 'count']
    ).properties(
        title='Count by Type'
    )

    # create scatter chart with duration and added year
    scatter_chart = alt.Chart(country_data).mark_point().encode(
        x=alt.X('date_added', title='Date Added'),
        y=alt.Y('duration', title='Duration(mins/seasons)'),
        color=alt.condition(brush, 'type:N', alt.value('lightgrey')),
        #color=alt.Color('type',scale=alt.Scale(scheme='category20'), legend=None),
        tooltip=['title', 'type', 'date_added', 'duration']
    ).properties(
        title='Date Added vs. Duration'
    ).add_selection(
        brush
    )


    # link the bar chart and the scatter chart
    linked_chart = alt.selection_single(fields=['type'], bind='legend')
    scatter_chart = scatter_chart.add_selection(linked_chart).transform_filter(linked_chart)
 
    # get the top 10 countries with highest count 
    top_countries = df['country'].value_counts().head(10).index.tolist()

    # create the drop down bar
    type_select = pn.widgets.Select(name='Select a type', options=['Movie', 'TV Show'], value='TV Show')
    country_select = pn.widgets.Select(name='Select a country', options=top_countries)
    
    # create with panel 
    plots = pn.Row(pn.Column('#Country,type and duration'),
                   pn.Column(bar_chart, scatter_chart))

    return plots


In [24]:
# get the top 10 countries with highest count 
top_countries = df['country'].value_counts().head(10).index.tolist()

# create the drop down bar
type_select = pn.widgets.Select(name='Select a type', options=['Movie', 'TV Show'], value='TV Show')
country_select = pn.widgets.Select(name='Select a country', options=top_countries)
year_range_slider = pn.widgets.RangeSlider(name='Release Year Range', start=df['added_year'].min(),
                                           end=df['added_year'].max(), step=1, value=(df['added_year'].min(), df['release_year'].max()))

type_select
country_select
year_range_slider

RangeSlider(end=2021, name='Release Year Range', start=2008, step=1, value=(2008, 2021), value_end=2021, value_start=2008)

## About
The visualization focuses on the exploration of the information about the duration of the different type of movies/TV shows and their added year to Netflix

We would like to demonsrate the development of movies/tv shows in each country 

## Example analysis 
The United States has the most products on Netflix and it also has the longest TV shows (17 seasons); even though the India products takes the second largest propotion in Netflix, it only has 81 TV shows on Netflix and the longest one are 3 seasons. 

## How to Use
Select **countries** that you would like to investigate

Select **type** of Netflix you would like to investigate 

Select a specific **year** interval that you are interested in

## Limitation
Based on this part, we can choose the country and type from the dropdown bar and investigate the details information for each country, but it quite difficult to compare one to another. 

In [25]:
panel = pn.interact(generate_plots, country_name=country_select, type_name=type_select, year_range=year_range_slider)

panel

Column
    [0] Column
        [0] Select(options=['United States', ...], value='United States')
        [1] Select(options=['Movie', 'TV Show'], value='TV Show')
        [2] RangeSlider(end=2021, name='Release Year Range', start=2008, step=1, value=(2008, 2021), value_end=2021, value_start=2008)
    [1] Row
        [0] Row
            [0] Column
                [0] Markdown(str)
            [1] Column
                [0] Vega(Chart, selection=Selection)
                [1] Vega(Chart, selection=Selection)

In [45]:
app1 = panel.servable('app1')
app1

Column
    [0] Column
        [0] Select(options=['United States', ...], value='United States')
        [1] Select(options=['Movie', 'TV Show'], value='TV Show')
        [2] RangeSlider(end=2021, name='Release Year Range', start=2008, step=1, value=(2008, 2021), value_end=2021, value_start=2008)
    [1] Row
        [0] Row
            [0] Column
                [0] Markdown(str)
            [1] Column
                [0] Vega(Chart, selection=Selection)
                [1] Vega(Chart, selection=Selection)

# PART 2


In [30]:
# -*- coding: utf-8 -*-
"""DV-assignment_3.ipynb

Automatically generated by Colaboratory.

Original file is located at
    https://colab.research.google.com/drive/1eB4h2jdNNni05nwRAEYtbHBZ82J1kHR_
"""

import pandas as pd
import altair as alt
from altair import expr, datum
from altair import expr, datum
import numpy as np
import panel as pn
from panel.interact import interact
pn.extension()
pn.extension('vega')
alt.data_transformers.enable('default', max_rows=None)

df = pd.read_csv('netflix1.csv')
#print(df.head())
#print(df.shape)

In [31]:
# seperate movies and TV shows
movie_df = df[df['type'] == 'Movie']
tv_df = df[df['type'] == 'TV Show']


# TV show charts 
# create a column that counts the number of tv shows released per year/rating
# group the DataFrame by release year, rating, and count the number of TV shows
count_df = tv_df.groupby(['release_year', 'rating']).size().reset_index(name='count')

# display the resulting DataFrame
print(count_df.head())

   release_year rating  count
0          1925  TV-14      1
1          1945  TV-MA      1
2          1946  TV-14      1
3          1963  TV-14      1
4          1967   TV-G      1


In [ ]:
# create a size scale based on the 'count' column
size_scale = alt.Scale(domain=(0, count_df['count'].max()), range=(50, 500))

# create the chart with a size encoding based on the 'count' column
chart = alt.Chart(count_df).mark_point().encode(
    x=alt.X('release_year', scale=alt.Scale(domain=(1920, 2022))),
    y='rating',
    color=alt.Color('rating:N', scale=alt.Scale(scheme='Viridis')),
    tooltip=['rating:N', 'count:Q'],
    size=alt.Size('count:Q', scale=size_scale)
).interactive()

# display the chart
chart

In [33]:
chart.to_dict().keys()
chart.to_dict()['selection']

# single seletion with zooming
size_scale = alt.Scale(domain=(0, count_df['count'].max()), range=(10, 500))
brush = alt.selection(type='single', encodings=['x','y'])

chart = alt.Chart(count_df).mark_point().encode(
    x=alt.X('release_year', scale=alt.Scale(domain=(1920, 2022))),
    y='rating',
    color=alt.condition(brush, alt.Color('rating:N', scale=alt.Scale(scheme='Viridis')), alt.value('lightgray')),
    tooltip=['rating:N', 'count:Q'],
    size=alt.Size('count:Q', scale=size_scale)
).interactive().add_selection(brush)

chart


alt.Chart(...)

In [34]:
# interval selection
size_scale = alt.Scale(domain=(0, count_df['count'].max()), range=(10, 500))
brush = alt.selection(type='interval', encodings=['x','y'])

chart = alt.Chart(count_df).mark_point().encode(
    x=alt.X('release_year', scale=alt.Scale(domain=(1920, 2022))),
    y='rating',
    color=alt.condition(brush, alt.Color('rating:N', scale=alt.Scale(scheme='Viridis')), alt.value('lightgray')),
    tooltip=['rating:N', 'count:Q'],
    size=alt.Size('count:Q', scale=size_scale)
).add_selection(brush)

chart


alt.Chart(...)

In [40]:
# interval selection
brush = alt.selection(type='interval', encodings=['x','y'])

# create box chart
box_chart = alt.Chart(count_df).transform_filter(
    brush
).mark_boxplot().encode(
    x='rating:N',
    y='count:Q',
    color='rating:N'
)

# create scatter plot with interval selection
size_scale = alt.Scale(domain=(0, count_df['count'].max()), range=(10, 700))

scatter_plot = alt.Chart(count_df).mark_point().encode(
    y='rating',
    x=alt.X('release_year', scale=alt.Scale(domain=(1920, 2022))),
    tooltip=['rating:N', 'count:Q'],
    size=alt.Size('count:Q', scale=size_scale),
    color=alt.condition(brush, alt.Color('rating:N', scale=alt.Scale(scheme='Viridis')), alt.value('lightgray'))
).add_selection(brush)

# set chart properties
scatter_plot = scatter_plot.properties(
    width=500,  
    height=300 
)

# combine scatter plot and line chart
combined_chart = scatter_plot | box_chart
combined_chart

alt.HConcatChart(...)

In [41]:
# same form of chart for the movies
# create a column that counts the number of movies released per year/rating
count_df_movie = movie_df.groupby(['release_year', 'rating']).size().reset_index(name='count')

# display the resulting DataFrame
print(count_df_movie.head())

   release_year rating  count
0          1942  TV-14      2
1          1943  TV-PG      3
2          1944  TV-14      2
3          1944  TV-PG      1
4          1945  TV-14      2


In [42]:
# interval selection
brush = alt.selection(type='interval', encodings=['x','y'])

# create box chart
box_chart_movie = alt.Chart(count_df_movie).transform_filter(
    brush
).mark_boxplot().encode(
    x='rating:N',
    y='count:Q',
    color='rating:N'
)

# create scatter plot with interval selection
size_scale = alt.Scale(domain=(0, count_df_movie['count'].max()), range=(10, 700))

scatter_plot_movie = alt.Chart(count_df_movie).mark_point().encode(
    y='rating',
    x=alt.X('release_year', scale=alt.Scale(domain=(1920, 2022))),
    tooltip=['rating:N', 'count:Q'],
    size=alt.Size('count:Q', scale=size_scale),
    color=alt.condition(brush, alt.Color('rating:N', scale=alt.Scale(scheme='Category10')), alt.value('lightgray'))
).add_selection(brush)

# set chart properties
scatter_plot_movie = scatter_plot_movie.properties(
    width=500,  
    height=300 
)

# combine scatter plot and line chart
movie_chart = scatter_plot_movie | box_chart_movie
movie_chart

alt.HConcatChart(...)

In [49]:
text = "This is the TV chart."
text_pane = pn.pane.Markdown(text)

chart_pane = pn.panel(combined_chart, height=100, sizing_mode='scale_width')

app2 = pn.Column(
    '# TV show Chart', 
    text_pane,
    chart_pane
)

app2.servable('app2')

text = "This is the movie chart."
text_pane = pn.pane.Markdown(text)

chart_pane = pn.panel(movie_chart, height=100, sizing_mode='scale_width')

app3 = pn.Column(
    '# Movie Chart',
    text_pane,
    chart_pane
)

import param

app4 = pn.Column(
    app2, 
    app3, 
    spacing=param.Parameter(default=1, doc='The spacing between panes.'),
    sizing_mode='stretch_width'
)

app4.servable()


Column(sizing_mode='stretch_width')
    [0] Column
        [0] Markdown(str)
        [1] Markdown(str)
        [2] Vega(HConcatChart, height=100, selection=Selection, sizing_mode='scale_width')
    [1] Column
        [0] Markdown(str)
        [1] Markdown(str)
        [2] Vega(HConcatChart, height=100, selection=Selection, sizing_mode='scale_width')

# PART 3

In [50]:
netflix = pd.read_csv('netflix1.csv')

alt.data_transformers.enable('default', max_rows=None)

DataTransformerRegistry.enable('default')

In [51]:
recent_years = netflix[netflix['release_year'] >= 2010]

top_countries = recent_years.groupby('country').size().reset_index(name='count').nlargest(10, 'count')['country']
top_movies = recent_years[recent_years['country'].isin(top_countries)]

counts = top_movies.groupby(['country', 'release_year']).size().reset_index(name='count')
counts['release_year_datetime'] = pd.to_datetime(counts['release_year'], format='%Y')
counts

country  release_year  count release_year_datetime
0           Canada          2010      6            2010-01-01
1           Canada          2011      4            2011-01-01
2           Canada          2012      5            2012-01-01
3           Canada          2013      3            2013-01-01
4           Canada          2014     19            2014-01-01
..             ...           ...    ...                   ...
114  United States          2017    383            2017-01-01
115  United States          2018    394            2018-01-01
116  United States          2019    385            2019-01-01
117  United States          2020    355            2020-01-01
118  United States          2021    168            2021-01-01

[119 rows x 4 columns]

In [52]:
selector = alt.selection_single(fields=['country'], on='mouseover', empty='none')

chart = alt.Chart(counts).mark_area().encode(
    x='release_year_datetime:T',
    y='count:Q',
    color='country:N',
    tooltip=[alt.Tooltip('country:N', title='Country'), alt.Tooltip('release_year:Q', title='Year'), alt.Tooltip('count:Q', title='Number of Movies')],
    opacity=alt.condition(selector, alt.value(1), alt.value(0.2))
).add_selection(selector)

chart

alt.Chart(...)

In [54]:
counts['growth'] = counts.groupby('country')['count'].diff()
counts['growth'].fillna(value=0, inplace=True)
counts['percent'] = counts.groupby('country')['count'].apply(lambda x: x / x.sum())

table_count = alt.Chart(counts).transform_filter(selector).mark_text().encode(
    x=alt.X('release_year_datetime:T', title='Year'),
    y=alt.Y('country:N', title='Number'),
    text='count:Q'
).properties(width=500)

table_diff = alt.Chart(counts).transform_filter(selector).mark_text().encode(
    x=alt.X('release_year_datetime:T', title='Year'),
    y=alt.Y('country:N', title='Increased Number'),
    text=alt.Text('growth:Q', format='+')
).properties(width=500)

table_pct = alt.Chart(counts).transform_filter(selector).mark_text().encode(
    x=alt.X('release_year_datetime:T', title='Year'),
    y=alt.Y('country:N', title='Percentage'),
    text=alt.Text('percent:Q', format='.1%')
).properties(width=500)

table = alt.vconcat(table_count, table_diff, table_pct, spacing=5).resolve_scale(x='shared')

chart | table

<ipython-input-54-7a3d6f074949>:3: FutureWarning: Not prepending group keys to the result index of transform-like apply. In the future, the group keys will be included in the index, regardless of whether the applied function returns a like-indexed object.
To preserve the previous behavior, use

	>>> .groupby(..., group_keys=False)

To adopt the future behavior and silence this warning, use 

	>>> .groupby(..., group_keys=True)
  counts['percent'] = counts.groupby('country')['count'].apply(lambda x: x / x.sum())


alt.HConcatChart(...)

In [57]:
text = "This is Xiaohan's chart."
text_pane_5 = pn.pane.Markdown(text)
chart_pane_5 = pn.panel(chart | table, height=100, sizing_mode='scale_width')

app5 = pn.Column(
    '# Xiaohan Chart', 
    text_pane_5,
    chart_pane_5
)

app5.servable('app5')

Column
    [0] Markdown(str)
    [1] Markdown(str)
    [2] Vega(HConcatChart, height=100, selection=Selection, sizing_mode='scale_width')